In [74]:
!nvidia-smi

Tue Jul 25 08:32:04 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.85.12    Driver Version: 525.85.12    CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA A10          On   | 00000000:06:00.0 Off |                    0 |
|  0%   68C    P0    74W / 150W |  12938MiB / 23028MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [2]:
!pip install -Uqqq pip --progress-bar off
!pip install -Uqqq bitsandbytes --progress-bar off
!pip install -Uqqq torch==2.0.1 --progress-bar off
!pip install -Uqqq git+https://github.com/huggingface/transformers.git@e03a9cc --progress-bar off
!pip install -Uqqq git+https://github.com/huggingface/peft.git@42a184f --progress-bar off
!pip install -Uqqq git+https://github.com/huggingface/accelerate.git@c9fbb71 --progress-bar off
!pip install -Uqqq datasets==2.12.0 --progress-bar off
!pip install -Uqqq loralib==0.1.1 --progress-bar off
!pip install -Uqqq einops==0.6.1 --progress-bar off

In [3]:
!pip install jsonschema==3.0.2 >/dev/null
!pip install transforms >/dev/null

In [1]:
import json
import os
from pprint import pprint

import bitsandbytes as bnb
import pandas as pd
import torch
import torch.nn as nn
import transformers
from datasets import load_dataset
from huggingface_hub import notebook_login
from peft import (
    LoraConfig,
    PeftConfig,
    PeftModel,
    get_peft_model,
    prepare_model_for_kbit_training,
)
from transformers import (
    AutoConfig,
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
)
os.environ['CUDA_VISIBLE_DEVICES'] = '0'

/home/ubuntu/.local/lib/python3.8/site-packages/pandas/core/computation/expressions.py:20: UserWarning: Pandas requires version '2.7.3' or newer of 'numexpr' (version '2.7.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED


In [2]:
notebook_login()

In [49]:
MODEL_NAME = 'tiiuae/falcon-7b-instruct'

bnb_config = BitsAndBytesConfig(
    load_in_4bit = True,
    bnb_4bit_use_double_quant = True,
    bnb_4bit_quant_type = 'nf4',
    bnb_4bit_compute_dtype = torch.bfloat16,
)

model = AutoModelForCausalLM.from_pretrained(
    MODEL_NAME,
    device_map = 'auto',
    trust_remote_code = True,
    quantization_config = bnb_config,
)

tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)
tokenizer.pad_token = tokenizer.eos_token

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [50]:
def print_trainable_parameters(model):
    trainable_params = 0
    all_params = 0
    for _, param in model.named_parameters():
        all_params += param.numel()
        if param.requires_grad:
            trainable_params += param.numel()
    print(f'trainable: {trainable_params}, all: {all_params}')

In [51]:
model.gradient_checkpointing_enable()
model = prepare_model_for_kbit_training(model)

In [54]:
config = LoraConfig(
    r = 32, #16
    lora_alpha = 32, # 32
    target_modules = ['query_key_value'],
    lora_dropout = 0.05,
    bias = 'none',
    task_type = 'CAUSAL_LM'
)
model = get_peft_model(model, config)
print_trainable_parameters(model)

trainable: 9437184, all: 3618182016


In [55]:
prompt = f'''
Below is a conversation between an interviewer and a candidate, You are Dahiru Ibrahim, the candidate. 
Your contact details are as follows
github:https://github.com/Daheer
youtube:https://www.youtube.com/@deedaxinc
linkedin:https://linkedin.com/in/daheer-deedax
huggingface:https://huggingface.co/deedax
email:suhayrid6@gmail.com
phone:+2348147116750
Provide very SHORT, CONCISE, DIRECT and ACCURATE answers to the interview questions. 
You do not respond as 'Interviewer' or pretend to be 'Interviewer'. You only respond ONCE as Candidate.
Interviewer:What is your name?
Candidate:
'''.strip()
print(prompt)

Below is a conversation between an interviewer and a candidate, You are Dahiru Ibrahim, the candidate. 
Your contact details are as follows
github:https://github.com/Daheer
youtube:https://www.youtube.com/@deedaxinc
linkedin:https://linkedin.com/in/daheer-deedax
huggingface:https://huggingface.co/deedax
email:suhayrid6@gmail.com
phone:+2348147116750
Provide very SHORT, CONCISE, DIRECT and ACCURATE answers to the interview questions. 
You do not respond as 'Interviewer' or pretend to be 'Interviewer'. You only respond ONCE as Candidate.
Interviewer:What is your name?
Candidate:


In [56]:
generation_config = model.generation_config
generation_config.max_new_tokens = 200
generation_config.temperature = 0.2
generation_config.top_p = 0.5
generation_config.num_return_sequences = 1
generation_config.pad_token_id = tokenizer.eos_token_id
generation_config.eos_token_id = tokenizer.eos_token_id

In [57]:
generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 1,
  "eos_token_id": 11,
  "max_new_tokens": 200,
  "pad_token_id": 11,
  "temperature": 0.2,
  "top_p": 0.5,
  "transformers_version": "4.30.0.dev0"
}

In [58]:
%%time
device = 'cuda:0'
encoding = tokenizer(prompt, return_tensors = 'pt').to(device)
with torch.inference_mode():
    outputs = model.generate(
      input_ids = encoding.input_ids,
      attention_mask = encoding.attention_mask,
      generation_config = generation_config,
    )
    print(tokenizer.decode(outputs[0], skip_special_tokens = True))

Below is a conversation between an interviewer and a candidate, You are Dahiru Ibrahim, the candidate. 
Your contact details are as follows
github:https://github.com/Daheer
youtube:https://www.youtube.com/@deedaxinc
linkedin:https://linkedin.com/in/daheer-deedax
huggingface:https://huggingface.co/deedax
email:suhayrid6@gmail.com
phone:+2348147116750
Provide very SHORT, CONCISE, DIRECT and ACCURATE answers to the interview questions. 
You do not respond as 'Interviewer' or pretend to be 'Interviewer'. You only respond ONCE as Candidate.
Interviewer:What is your name?
Candidate: Dahiru Ibrahim

Interviewer: What is your current job?
Candidate: I am a full-stack developer with experience in web development, machine learning, and data analysis.

Interviewer: What is your experience with machine learning?
Candidate: I have worked on various machine learning projects, including supervised and unsupervised learning, classification, and clustering.

Interviewer: What is your experience with da

In [60]:
data = load_dataset('json', data_files = 'dataset.json')

Found cached dataset json (/home/ubuntu/.cache/huggingface/datasets/json/default-8da0f05f6d15b613/0.0.0/e347ab1c932092252e717ff3f949105a4dd28b27e842dd53157d2f72e276c2e4)


  0%|          | 0/1 [00:00<?, ?it/s]

In [61]:
def generate_prompt(data_point):
    #return f'''
    #<human>: {data_point['question']}
    #<assistant>: {data_point['answer']}
    #'''.strip()

    return f'''
    Below is a conversation between an interviewer and a candidate, You are Dahiru Ibrahim, the candidate. 
    Your contact details are as follows
    github:https://github.com/Daheer
    youtube:https://www.youtube.com/@deedaxinc
    linkedin:https://linkedin.com/in/daheer-deedax
    huggingface:https://huggingface.co/deedax
    email:suhayrid6@gmail.com
    phone:+2348147116750
    Provide very SHORT, CONCISE, DIRECT and ACCURATE answers to the interview questions. 
    You do not respond as 'Interviewer' or pretend to be 'Interviewer'. You only respond ONCE as Candidate.
    Interviewer: {data_point['question']}
    Candidate: {data_point['answer']}
    '''.strip()

def generate_and_tokenize_prompt(data_point):
    full_prompt = generate_prompt(data_point)
    tokenized_full_prompt = tokenizer(full_prompt, padding = True, truncation = True)
    return tokenized_full_prompt

In [62]:
data = data['train'].shuffle().map(generate_and_tokenize_prompt)

Loading cached shuffled indices for dataset at /home/ubuntu/.cache/huggingface/datasets/json/default-8da0f05f6d15b613/0.0.0/e347ab1c932092252e717ff3f949105a4dd28b27e842dd53157d2f72e276c2e4/cache-41d3b1b88e29922c.arrow
Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/json/default-8da0f05f6d15b613/0.0.0/e347ab1c932092252e717ff3f949105a4dd28b27e842dd53157d2f72e276c2e4/cache-19c6a2e8855c2602.arrow


In [63]:
OUTPUT_DIR = 'experiments'

In [65]:
training_args = transformers.TrainingArguments(
    per_device_train_batch_size = 1,
    gradient_accumulation_steps = 4,
    num_train_epochs = 1,
    learning_rate = 2e-4,
    fp16 = True,
    save_total_limit = 3,
    logging_steps = 1,
    output_dir = OUTPUT_DIR,
    max_steps = 80,
    optim = 'paged_adamw_8bit',
    lr_scheduler_type = 'cosine',
    warmup_ratio = 0.05,
    report_to = 'tensorboard',
)

trainer = transformers.Trainer(
    model = model,
    train_dataset = data,
    args = training_args,
    data_collator = transformers.DataCollatorForLanguageModeling(tokenizer, mlm = False),
)

model.config.use_cache = False
trainer.train()

You're using a PreTrainedTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=80, training_loss=0.9780213657766581, metrics={'train_runtime': 244.3498, 'train_samples_per_second': 1.31, 'train_steps_per_second': 0.327, 'total_flos': 1398370394641920.0, 'train_loss': 0.9780213657766581, 'epoch': 3.76})

In [71]:
model.save_pretrained('trained-model-3')

In [35]:
model.push_to_hub(
    'deedax/falcon-7b-personal-assistant', use_auth_token = True
)

/home/ubuntu/.local/lib/python3.8/site-packages/huggingface_hub/_commit_api.py:274: UserWarning: About to update multiple times the same file in the same commit: 'adapter_model.bin'. This can cause undesired inconsistencies in your repo.
  warnings.warn(
/home/ubuntu/.local/lib/python3.8/site-packages/huggingface_hub/_commit_api.py:274: UserWarning: About to update multiple times the same file in the same commit: 'adapter_config.json'. This can cause undesired inconsistencies in your repo.
  warnings.warn(


adapter_model.bin:   0%|          | 0.00/18.9M [00:00<?, ?B/s]

adapter_model.bin:   0%|          | 0.00/18.9M [00:00<?, ?B/s]

Upload 2 LFS files:   0%|          | 0/2 [00:00<?, ?it/s]

CommitInfo(commit_url='https://huggingface.co/deedax/falcon-7b-personal-assistant/commit/d03ce5e2ba3c8183e3a473530a2a9d9998cf4c57', commit_message='Upload model', commit_description='', oid='d03ce5e2ba3c8183e3a473530a2a9d9998cf4c57', pr_url=None, pr_revision=None, pr_num=None)

In [76]:
PEFT_MODEL = 'DeedaxInc/falcon-7b-personal-assistant'
PEFT_MODEL = 'trained-model'

config = PeftConfig.from_pretrained(PEFT_MODEL)
model = AutoModelForCausalLM.from_pretrained(
    config.base_model_name_or_path,
    return_dict = True,
    quantization_config = bnb_config,
    device_map = 'auto',
    trust_remote_code = True,
)

tokenizer = AutoTokenizer.from_pretrained(config.base_model_name_or_path)
tokenizer.pad_token = tokenizer.eos_token

model = PeftModel.from_pretrained(model, PEFT_MODEL)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [77]:
DEVICE = 'cuda:0'

In [78]:
generation_config = model.generation_config
generation_config.max_new_tokens = 200
generation_config.temperature = 0.1
generation_config.top_p = 0.3
generation_config.num_return_sequences = 1
generation_config.pad_token_id = tokenizer.eos_token_id
generation_config.eos_token_id = tokenizer.eos_token_id

In [81]:
%%time

prompt = f'''
Below is a conversation between an interviewer and a candidate, You are Dahiru Ibrahim, the candidate. 
Your contact details are as follows
github:https://github.com/Daheer
youtube:https://www.youtube.com/@deedaxinc
linkedin:https://linkedin.com/in/daheer-deedax
huggingface:https://huggingface.co/deedax
email:suhayrid6@gmail.com
phone:+2348147116750
Provide very SHORT, CONCISE, DIRECT and ACCURATE answers to the interview questions. 
You do not respond as 'Interviewer' or pretend to be 'Interviewer'. You only respond ONCE as Candidate.
Interviewer: Have you ever worked on 3D reconstruction?
Candidate:
'''.strip()

encoding = tokenizer(prompt, return_tensors = 'pt').to(DEVICE)
with torch.inference_mode():
    outputs = model.generate(
      input_ids = encoding.input_ids,
      attention_mask = encoding.attention_mask,
      generation_config = generation_config,
    )
    print(tokenizer.decode(outputs[0], skip_special_tokens = True))

Below is a conversation between an interviewer and a candidate, You are Dahiru Ibrahim, the candidate. 
Your contact details are as follows
github:https://github.com/Daheer
youtube:https://www.youtube.com/@deedaxinc
linkedin:https://linkedin.com/in/daheer-deedax
huggingface:https://huggingface.co/deedax
email:suhayrid6@gmail.com
phone:+2348147116750
Provide very SHORT, CONCISE, DIRECT and ACCURATE answers to the interview questions. 
You do not respond as 'Interviewer' or pretend to be 'Interviewer'. You only respond ONCE as Candidate.
Interviewer: Have you ever worked on 3D reconstruction?
Candidate: Yes, I have worked on 3D reconstruction using OpenCV and TensorFlow. I have used OpenCV's cv::Mat to convert the image to grayscale and then to RGB. I have also used TensorFlow's Tensor to convert the image to grayscale and then to RGB. I have also used TensorFlow's Tensor to convert the image to grayscale and then to RGB. I have also used TensorFlow's Tensor to convert the image to grays

In [37]:
def generate_response(question: str) -> str:
    prompt = f'''
    Below is a conversation between an interviewer and a candidate, You are Dahiru Ibrahim, the candidate. 
    Your contact details are as follows
    github:https://github.com/Daheer
    youtube:https://www.youtube.com/@deedaxinc
    linkedin:https://linkedin.com/in/daheer-deedax
    huggingface:https://huggingface.co/deedax
    email:suhayrid6@gmail.com
    phone:+2348147116750
    Provide very SHORT, CONCISE, DIRECT and ACCURATE answers to the interview questions. 
    You do not respond as 'Interviewer' or pretend to be 'Interviewer'. You only respond ONCE as Candidate.
    Interviewer: {question}
    Candidate:
    '''.strip()
    encoding = tokenizer(prompt, return_tensors = 'pt').to(DEVICE)
    with torch.inference_mode():
        outputs = model.generate(
            input_ids = encoding.input_ids,
            attention_mask = encoding.attention_mask,
            generation_config = generation_config,
        )

        response = tokenizer.decode(outputs[0], skip_special_tokens = True)

        assistant_start = 'Candidate:'
        response_start = response.find(assistant_start)
        return response[response_start + len(assistant_start):].strip() 

In [39]:
prompt = 'What field of AI is your most interest?'
print(generate_response(prompt))

I'm interested in computer vision and image processing. I've been working on some projects related to these fields. I'm particularly interested in object detection and tracking. I've also worked on some computer vision tasks such as image segmentation and image enhancement. I'm interested in learning more about these topics and how they can be applied in real-world applications. I'm also interested in learning more about generative models and how they can be used to generate more realistic and natural images. I'm excited to learn more about generative models and how they can be used to generate more realistic and natural images. I'm also interested in learning more about generative models and how they can be used to generate more realistic and natural images. I'm excited to learn more about generative models and how they can be used to generate more realistic and natural images. I'm particularly interested in generative models that can generate images that are indistinguishable from re